In [98]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
sns.set()
import requests
import plotly.express as px
import plotly.graph_objects as go
%matplotlib inline

# Layout for plotly figure exports
layout = dict(font=dict(family='Computer Modern',size=11),
              margin=dict(l=5, r=5, t=30, b=5),
              width=605, height= 250)

path = '/Users/davidipsen/Documents/DTU/5. Semester (MSc)/Thesis  -  SmartCharge'
pathhtml = '/Users/davidipsen/Documents/DTU/5. Semester (MSc)/Thesis  -  SmartCharge/plots/_figures'
fetch = True
tz = 'HourDK' # or 'HourDK'

In [99]:
##### Fetch data from EnergiNet
if fetch:
    ### Spot prices [DKK/MWh].
    # Divide by 1000 to get DKK/kWh.
    nrows = 150000
    response = requests.get(
        url='https://api.energidataservice.dk/dataset/Elspotprices?limit=' + str(nrows))
    result = response.json()
    df = pd.DataFrame.from_dict(result.get('records', []))

    # Preprocess
    #df.drop(['HourUTC'], axis=1, inplace=True)
    df = df[(df['PriceArea'] == 'DK1') | (df['PriceArea'] == 'DK2')] # Focus on DK

    ### CO2 [g/kWh]
    nrows = 1300000
    response = requests.get(
        url='https://api.energidataservice.dk/dataset/CO2Emis?limit=' + str(nrows))
    result = response.json()
    dfco2 = pd.DataFrame(result.get('records', []))

    # Preprocess
    dfco2.drop(['Minutes5UTC'], axis=1, inplace=True)
    dfco2 = dfco2[dfco2['PriceArea'] == 'DK1'] # Since CO2(DK1) = CO2(DK2), drop DK2

In [100]:
# Convert to DateTime
df['HourDK'] = pd.to_datetime(df['HourDK'])
dfco2['Minutes5DK'] = pd.to_datetime(dfco2['Minutes5DK'])

### Export dfs as csv
try:
    df.to_csv(path + '/data/spotprice/df_spot.csv', index=False)
    dfco2.to_csv(path + '/data/spotprice/df_co2.csv', index=False)
except:
    df = pd.read_csv(path + '/data/spotprice/df_spot.csv')
    dfco2 = pd.read_csv(path + '/data/spotprice/df_co2.csv')

In [101]:
## Show spotprices today
df_today = df[df['HourDK'].dt.date == pd.to_datetime('today').date()]
# Plot spot prices using plotly
fig = px.line(df_today, x='HourDK', y='SpotPriceDKK', color='PriceArea')
fig.update_yaxes(range=[0, 5000])
# Add labels
fig.update_layout(
    title='Spot prices' + ' ' + pd.to_datetime('today').date().strftime('%d-%m-%Y'),
    xaxis_title='Time',
    yaxis_title='Price [DKK/MWh]')
fig.show()


In [102]:
## Subset data for this month and only DK2 and export .csv
if fetch:
    df_sept22 = df[df[tz] >= '2022-09-01']
    df_sept22_DK2 = df_sept22[df_sept22['PriceArea'] == 'DK2']
    df_sept22_DK2.to_csv(path + '/data/spotprice/df_spot_since_sept22_' + tz + '.csv', index=False)

## Subset data for this year
if fetch:
    df_2022 = df[df[tz] >='2022-01-01']
    df_2022_DK2 = df_2022[df_2022['PriceArea'] == 'DK2']
    df_2022_DK2.to_csv(path + '/data/spotprice/df_spot_2022.csv', index=False)

# Basic Data Visualization

In [103]:
fig = px.line(df, x='HourDK', y='SpotPriceEUR', color='PriceArea', title='Historical Spot Prices', labels={'HourDK': 'Time', 'SpotPriceEUR': 'Price   [EUR/MWh]'})
# Make linewidth smaller
fig.update_traces(line=dict(width=0.9))
# Export figure both as html and pdf. Size: width=16cm, height=6.6cm
fig.show()
fig.write_html(pathhtml + '/spotprices.html')
fig.update_layout(layout)
fig.write_image(path + '/plots/spotprices/spotprices.pdf')

# Zoom in on period from 2022-12-12 to 2022-12-18
df_zoom = df[(df['HourDK'] >= '2022-12-12') & (df['HourDK'] <= '2022-12-19')]
fig = px.line(df_zoom, x='HourDK', y='SpotPriceEUR', color='PriceArea', title='Historical Spot Prices - a typical week', labels={'HourDK': 'Time', 'SpotPriceEUR': 'Price   [EUR/MWh]'})
# Make linewidth smaller
fig.update_traces(line=dict(width=0.9))
# Export figure both as html and pdf. Size: width=16cm, height=6.6cm
fig.update_layout(layout)
fig.update_layout(width=605*1.05)
fig.write_image(path + '/plots/spotprices/spotprices-zoom.pdf')
fig.show()

#### Aggregate 5 min intervals to 1 hours intervals for CO2 data

In [104]:
# Aggregate CO2 from 5 min to 1 hour
dfco2 = dfco2.groupby(pd.Grouper(key='Minutes5DK', freq='H')).mean()
dfco2.reset_index(inplace=True)
# Change name
dfco2.rename(columns={'Minutes5DK': 'HourDK'}, inplace=True)

In [105]:

# Create plot similiar to the one above for CO2
fig = px.line(dfco2, x='HourDK', y='CO2Emission', title='CO2 [g/kWh]', labels={'HourDK': 'Time', 'CO2Emission': 'CO2 [g/kWh]'})
fig.show()

In [106]:
# Merge the two dfs
D = pd.merge(df, dfco2, on='HourDK', how='inner')

## CO2 vs. spot price

In [164]:
firstTime = '2021-10-01'
lastTime = '2023-01-16'

Dsub = D[(D['HourDK'] >= firstTime) & (D['HourDK'] < lastTime)]
# Calculate Pearson's correlation
print("Pearson's linear correlation coefficient: ", Dsub['SpotPriceEUR'].corr(Dsub['CO2Emission'], method='pearson'))
print("Pearson's linear correlation coefficient: ", Dsub['SpotPriceEUR'][Dsub['SpotPriceEUR'] < 300].corr(Dsub['CO2Emission'][Dsub['SpotPriceEUR'] < 300], method='pearson'), "  (for SpotPriceEUR < 300)")
print("Pearson's linear correlation coefficient: ", Dsub['SpotPriceEUR'][Dsub['SpotPriceEUR'] > 300].corr(Dsub['CO2Emission'][Dsub['SpotPriceEUR'] > 300], method='pearson'), "  (for SpotPriceEUR > 300)")

# Calculate Spearman's rank correlation
print("Spearman's rank correlation coefficient: ", Dsub['SpotPriceEUR'].corr(Dsub['CO2Emission'], method='spearman'))
print("Spearman's rank correlation coefficient: ", Dsub['SpotPriceEUR'][Dsub['SpotPriceEUR'] < 300].corr(Dsub['CO2Emission'][Dsub['SpotPriceEUR'] < 300], method='spearman'), "  (for SpotPriceEUR < 300)")
print("Spearman's rank correlation coefficient: ", Dsub['SpotPriceEUR'][Dsub['SpotPriceEUR'] > 300].corr(Dsub['CO2Emission'][Dsub['SpotPriceEUR'] > 300], method='spearman'), "  (for SpotPriceEUR > 300)")

# Make plot quadratic
# For dates display only day not hour
fig = px.scatter(Dsub, x='SpotPriceEUR', y='CO2Emission', title='CO2 vs. Spot price      (from ' + firstTime + ' to ' + lastTime + ')',
                labels={'SpotPriceEUR': 'Spot price [EUR/MWh]', 'CO2Emission': 'CO2 [g/kWh]'}, trendline='lowess',
                trendline_options=dict(frac=0.2))
fig.update_traces(marker=dict(opacity=0.05))
# Marker size
#fig.update_traces(marker=dict(size=4))
# Add rounded correlations directly to figure
fig.add_annotation(x=800, y=435, text="Pearson's r = " + str(round(Dsub['SpotPriceEUR'].corr(Dsub['CO2Emission']), 2)), showarrow=False)
fig.add_annotation(x=800, y=400, text="Pearson's r = " + str(round(Dsub['SpotPriceEUR'][Dsub['SpotPriceEUR'] < 300].corr(Dsub['CO2Emission'][Dsub['SpotPriceEUR'] < 300]), 2)) +"  (SpotPrice < 300)", showarrow=False)
fig.add_annotation(x=800, y=365, text="Pearson's r = " + str(round(Dsub['SpotPriceEUR'][Dsub['SpotPriceEUR'] > 300].corr(Dsub['CO2Emission'][Dsub['SpotPriceEUR'] > 300]), 2)) +"  (SpotPrice > 300)", showarrow=False)

# Add rounded Spearman's rank correlations directly to figure
fig.add_annotation(x=800, y=330-10, text="Spearman's ρ = " + str(round(Dsub['SpotPriceEUR'].corr(Dsub['CO2Emission'], method='spearman'), 2)), showarrow=False)
fig.add_annotation(x=800, y=295-10, text="Spearman's ρ = " + str(round(Dsub['SpotPriceEUR'][Dsub['SpotPriceEUR'] < 300].corr(Dsub['CO2Emission'][Dsub['SpotPriceEUR'] < 300], method='spearman'), 2)) +"  (SpotPrice < 300)", showarrow=False)
fig.add_annotation(x=800, y=260-10, text="Spearman's ρ = " + str(round(Dsub['SpotPriceEUR'][Dsub['SpotPriceEUR'] > 300].corr(Dsub['CO2Emission'][Dsub['SpotPriceEUR'] > 300], method='spearman'), 2)) +"  (SpotPrice > 300)", showarrow=False)

# Add labels
fig.data[-1].line.color = 'red'
fig.update_layout(layout)
# Add legend
fig.update_layout(legend=dict(
    yanchor="top",
    y=0.99,
    xanchor="left",
    x=0.01
))
#fig.update_layout(autosize=False, width=605, height=605)
fig.show()
fig.write_image(path + '/plots/spotprices/spotprice_vs_co2.pdf')

Pearson's linear correlation coefficient:  0.43773919602219635
Pearson's linear correlation coefficient:  0.5760922910542029   (for SpotPriceEUR < 300)
Pearson's linear correlation coefficient:  -0.07756363885817433   (for SpotPriceEUR > 300)
Spearman's rank correlation coefficient:  0.5598835353155175
Spearman's rank correlation coefficient:  0.6129041098015198   (for SpotPriceEUR < 300)
Spearman's rank correlation coefficient:  -0.050963726536228784   (for SpotPriceEUR > 300)


# SPOT PRICE PREDICTIONS - from Carnot.ai

In [44]:
pred1 = pd.read_excel(path + '/data/prediction_score_dk1.xlsx', parse_dates=True)
pred2 = pd.read_excel(path + '/data/prediction_score_dk2.xlsx', parse_dates=True)

# Preprocess data
pred1['dktime'] = pd.to_datetime(pred1['dktime'])
pred2['dktime'] = pd.to_datetime(pred2['dktime'])

# Drop variables "energysource", "utctime" and "latest"
pred1.drop(['energysource', 'utctime', 'latest'], axis=1, inplace=True)
pred2.drop(['energysource', 'utctime', 'latest'], axis=1, inplace=True)

# Show data
pred2

pricearea                    dktime   prediction  \
0          dk2 2022-08-31 16:00:00+02:00  4030.000000   
1          dk2 2022-08-31 17:00:00+02:00  4773.279785   
2          dk2 2022-08-31 18:00:00+02:00  5360.370117   
3          dk2 2022-08-31 19:00:00+02:00  5578.520020   
4          dk2 2022-08-31 20:00:00+02:00  5314.100098   
...        ...                       ...          ...   
3291       dk2 2022-09-23 20:00:00+02:00  1516.585473   
3292       dk2 2022-09-23 21:00:00+02:00  1109.752786   
3293       dk2 2022-09-23 22:00:00+02:00   967.133292   
3294       dk2 2022-09-23 23:00:00+02:00   956.245898   
3295       dk2 2022-09-24 00:00:00+02:00  1069.321496   

                    addedtime     id  
0     2022-08-31 15:07:12.848  26093  
1     2022-08-31 15:07:12.848  26094  
2     2022-08-31 15:07:12.848  26105  
3     2022-08-31 15:07:12.848  26112  
4     2022-08-31 15:07:12.848  26123  
...                       ...    ...  
3291  2022-09-17 22:44:09.744  62012  
3292  2022-09-17 22:44:09.744  62021  
3293  2022-09-17 22:44:09.744  62029  
3294  2022-09-17 22:44:09.744  62046  
3295  2022-09-17 22:44:09.744  62054  

[3296 rows x 5 columns]

In [43]:
# Count number of rows for each addedtime
pred2.groupby('addedtime').count()
# Forecasts starter fra 31. august 2022
# Forecaster ca. 6 dage frem.

for ptime in pred2['addedtime'].unique():
    px.line(pred2[pred2['addedtime'] == ptime], x='dktime', y='prediction', title='DK2: ' + ptime).show()
    # Add SpotPriceDKK from D to plot matching on HourDK == addedtime